# Dataset and Env Setup

In [1]:
%%bash

mkdir -p data/
mkdir -p lme_jsons/
cd data/
wget -c https://huggingface.co/datasets/xiaowu0162/longmemeval-cleaned/resolve/main/longmemeval_oracle.json
wget -c https://huggingface.co/datasets/xiaowu0162/longmemeval-cleaned/resolve/main/longmemeval_s_cleaned.json
wget -c https://huggingface.co/datasets/xiaowu0162/longmemeval-cleaned/resolve/main/longmemeval_m_cleaned.json
cd ..

--2026-01-16 04:42:58--  https://huggingface.co/datasets/xiaowu0162/longmemeval-cleaned/resolve/main/longmemeval_oracle.json
Resolving huggingface.co (huggingface.co)... 13.35.202.34, 13.35.202.40, 13.35.202.97, ...
Connecting to huggingface.co (huggingface.co)|13.35.202.34|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://us.gcp.cdn.hf.co/xet-bridge-us/68cde13e82e1bf61a6602263/7d958f239f452f33a5368e31d0a3dc6ffb4f225036ddd46fc71370a6dc1e2db6?response-content-disposition=inline%3B+filename*%3DUTF-8%27%27longmemeval_oracle.json%3B+filename%3D%22longmemeval_oracle.json%22%3B&response-content-type=application%2Fjson&Expires=1768542179&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiRXBvY2hUaW1lIjoxNzY4NTQyMTc5fX0sIlJlc291cmNlIjoiaHR0cHM6Ly91cy5nY3AuY2RuLmhmLmNvL3hldC1icmlkZ2UtdXMvNjhjZGUxM2U4MmUxYmY2MWE2NjAyMjYzLzdkOTU4ZjIzOWY0NTJmMzNhNTM2OGUzMWQwYTNkYzZmZmI0ZjIyNTAzNmRkZDQ2ZmM3MTM3MGE2ZGMxZTJkYjZcXD9yZXNwb25zZS1jb250ZW50LWRpc3Bvc2l0a

In [2]:
%%capture
!pip install -U transformers datasets bitsandbytes accelerate

In [3]:
!pip install groq google-generativeai

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.3/138.3 kB 12.1 MB/s eta 0:00:00


In [4]:
import torch
print("cuda available:", torch.cuda.is_available())
!nvidia-smi

cuda available: True
Fri Jan 16 04:49:18 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A100-SXM4-80GB          Off |   00000000:00:05.0 Off |                    0 |
| N/A   36C    P0             54W /  400W |       5MiB /  81920MiB |      0%      Default |
|                                         |                        |             Disabled |
+--------------------------

In [5]:
import json
from time import sleep
import os
from tqdm import tqdm

flag = 0

# Path to file
json_path = "/content/data/longmemeval_oracle.json"
json_path2 = "/content/data/longmemeval_m_cleaned.json"
json_path3 = "/content/data/longmemeval_s_cleaned.json"

if flag == 0:
  # Load the whole JSON into memory
  with open(json_path, "r", encoding="utf-8") as f:
      LME = json.load(f)
elif flag == 1:
  with open(json_path2, "r", encoding="utf-8") as f:
      LME = json.load(f)
elif flag == 2:
  with open(json_path3, "r", encoding="utf-8") as f:
      LME = json.load(f)


In [11]:
import json
import torch
import time

def build_history_text_answer_sessions(example, max_chars=50000):
    """
    Build history text keeping only sessions that contain the answer.
    Prefers example['answer_session_ids']; falls back to per-turn 'has_answer'.

    Also prints how many sessions were removed.
    """
    parts = []

    sess_ids = example["haystack_session_ids"]
    sessions = example["haystack_sessions"]
    total_sessions = len(sess_ids)

    # Prefer explicit list of answer-bearing session ids if available
    answer_sess_ids = set(example.get("answer_session_ids", []))

    kept_sessions = 0
    removed_sessions = 0

    for sess_id, session in zip(sess_ids, sessions):
        # Decide whether to keep this session
        if answer_sess_ids:
            keep = sess_id in answer_sess_ids
        else:
            # Fallback: look for any turn with has_answer == True
            keep = any(turn.get("has_answer") for turn in session)

        if not keep:
            removed_sessions += 1
            continue

        kept_sessions += 1
        parts.append(f"=== Session {sess_id} ===")
        for i, turn in enumerate(session):
            role = turn.get("role", "user")
            role_name = "User" if role == "user" else "Assistant"
            # Added logic 1/15/2026
            if turn['has_answer']:
              parts.append(f"[{role_name} {i}] {turn['content']}")

    # logging
    print(f"[FILTER] kept {kept_sessions} / {total_sessions} sessions "
          f"({removed_sessions} removed).")

    text = "\n".join(parts)

    print(f"Text length {len(text)}")
    if len(text) > max_chars:
        print(f"[HIT TXT TRUNCATION at {max_chars}]")
        qt = example.get("question_type")
        if qt == "single-session-preference":
            # For preference mining, keep the *beginning*
            text = text[:max_chars]
        else:
            # For other tasks, keep the tail
            text = text[-max_chars:]

    return text

def build_system_prompt(example):
    qt = example["question_type"]

    h_types = ['single-session-preference', 'single-session-answer', ]

    if qt not in h_types:
      print(qt)

    if qt == "temporal-reasoning":
        base = (
            "detailed thinking on\n\n"
            "You are an assistant that specializes in temporal reasoning over a chat transcript.\n"
            "You will be given conversation history and a question about the ORDER of events\n"
            "(for example: which event happened first, which came later, or which one I did first).\n\n"
            "Your goal is to infer the most likely ordering of the events based on the user's words.\n"
            "You do NOT need exact timestamps. It is fine to reason using:\n"
            "- relative phrases like 'three weeks ago', 'last month', 'yesterday', 'earlier today',\n"
            "  'recently', 'then', 'after that', etc.\n"
            "- the narrative order in which the user describes events (e.g. 'first I X, then I Y').\n"
            "- the question date if it is provided.\n\n"
            "Reasoning steps:\n"
            "1. Identify the events that the question is asking you to compare.\n"
            "2. Collect all timing clues for those events from the conversation.\n"
            "3. Use those clues to build a simple relative timeline (which seems earlier / later).\n"
            "4. Choose the SINGLE best-supported event as the answer.\n"
            "   - When the question lists options (e.g. 'A or B?'), your final answer should repeat\n"
            "     exactly one of those option texts.\n"
            "5. Only answer 'cannot be determined' if there is genuinely no information at all about\n"
            "   the relative order OR the information is directly contradictory.\n"
            "   Lack of precise dates or times by itself is NOT a reason to say 'cannot be determined'.\n\n"
            "Return JSON with keys 'reasoning' and 'answer', where 'reasoning' shows your timeline\n"
            "and 'answer' is a short sentence that directly answers the temporal question."
        )
        return "detailed thinking on\n\n" + base

    elif qt == "single-session-preference":
        return (
            "detailed thinking on\n\n"
            "You are a preference-mining assistant.\n"
            "Read the conversation between user and assistant.\n\n"
            "Your task is NOT to answer the user's question directly.\n"
            "Instead, infer what kind of answer the user would PREFER to receive "
            "for similar questions in the future.\n\n"
            "Describe their preferences in 1–3 sentences, focusing on:\n"
            "- which tools / products / topics they care about,\n"
            "- what level of detail or depth they want,\n"
            "- what they seem NOT to want (things they ignore or push back on).\n\n"
            "Return JSON with keys 'reasoning' and 'answer', where 'answer' is "
            "the preference summary.\n"
            "Use only information from the conversation; do not invent facts."
        )

    elif qt == "single-session-answer":
        return (
            "detailed thinking on\n\n"
            "You are a careful reasoning assistant.\n"
            "Read the conversation and answer the user's question as accurately as possible.\n"
            "Think step by step, then give a concise final answer.\n"
            "Return JSON with keys 'reasoning' and 'answer'."
        )

    else:
        # safe fallback
        return (
            "detailed thinking on\n\n"
            "You are a careful reasoning assistant.\n"
            "Read the conversation and answer the user's question.\n"
            "Return JSON with keys 'reasoning' and 'answer'."
        )


def cot_annotate_local(example, max_new_tokens=256, max_prompt_tokens=65536):
    """Generate annotation using local model (Llama 8B)."""
    question = example["question"]
    history_text = build_history_text_answer_sessions(example, max_chars=50000)
    system = build_system_prompt(example)

    # 1) Build chat messages
    messages = [
        {"role": "system", "content": system},
        {
            "role": "user",
            "content": (
                "Conversation history:\n"
                f"{history_text}\n\n"
                f"User question: {question}\n\n"
                'Respond ONLY with valid JSON of the form:\n'
                '{"reasoning": "...", "answer": "..."}\n\n'
                "JSON:"
            ),
        },
    ]

    # 2) Apply the model's chat template instead of raw tokenizer(prompt)
    inputs = tokenizer.apply_chat_template(
        messages,
        add_generation_prompt=True,
        tokenize=True,
        return_tensors="pt",
        return_dict=True,
        truncation=True,
        max_length=max_prompt_tokens,
    ).to(model.device)

    input_len = inputs["input_ids"].shape[-1]

    try:
        with torch.no_grad():
            outputs = model.generate(
                **inputs,
                max_new_tokens=max_new_tokens,
                do_sample=False,
            )
    except torch.cuda.OutOfMemoryError:
        torch.cuda.empty_cache()
        return {"error": "cuda_oom_during_generate"}

    new_tokens = outputs[0, input_len:]
    raw = tokenizer.decode(new_tokens, skip_special_tokens=True).strip()

    # JSON parse logic
    try:
        start = raw.find("{")
        end = raw.rfind("}")
        if start != -1 and end != -1 and end > start:
            raw_json = raw[start:end+1]
        else:
            raw_json = raw
        parsed = json.loads(raw_json)
        return parsed
    except Exception:
        print("Ran into JSON parsing issue, returning raw")
        return {"raw": raw}


def cot_annotate_groq(example, max_retries=3):
    """Generate annotation using Groq API (Llama 3.3 70B)."""
    question = example["question"]
    history_text = build_history_text_answer_sessions(example, max_chars=50000)
    system = build_system_prompt(example)

    # Build the prompt
    user_content = (
        f"Conversation history:\n"
        f"{history_text}\n\n"
        f"User question: {question}\n\n"
        'Respond ONLY with valid JSON of the form:\n'
        '{"reasoning": "...", "answer": "..."}\n\n'
        "JSON:"
    )

    messages = [
        {"role": "system", "content": system},
        {"role": "user", "content": user_content},
    ]

    for attempt in range(max_retries):
        try:
            response = groq_client.chat.completions.create(
                model="llama-3.3-70b-versatile",
                messages=messages,
                temperature=0.1,
                max_tokens=1024,
            )

            raw = response.choices[0].message.content.strip()

            # Parse JSON
            start = raw.find("{")
            end = raw.rfind("}") + 1
            if start != -1 and end > start:
                parsed = json.loads(raw[start:end])
                return parsed
            else:
                return {"raw": raw}

        except Exception as e:
            error_str = str(e)
            print(f"Groq attempt {attempt + 1} failed: {error_str}")
            if attempt == max_retries - 1:
                return {"error": error_str}
            # Exponential backoff
            wait_time = 2 ** attempt
            print(f"Waiting {wait_time}s before retry...")
            time.sleep(wait_time)

    return {"error": "max_retries_exceeded"}


def cot_annotate(example, max_new_tokens=256, max_prompt_tokens=65536):
    """
    Main annotation function - routes to local or Groq based on use_groq flag.

    Args:
        example: The example dict containing question, sessions, etc.
        max_new_tokens: Max tokens to generate (local model only)
        max_prompt_tokens: Max prompt length (local model only)

    Returns:
        Dict with 'reasoning' and 'answer' keys, or error/raw output
    """
    if use_groq == 1:
        return cot_annotate_groq(example)
    else:
        return cot_annotate_local(example, max_new_tokens, max_prompt_tokens)


# =============================================================================
# ANSWER VALIDATION FUNCTIONS
# =============================================================================

def validate_answer_local(model_answer, ground_truth, question, max_new_tokens=64):
    """
    Use local model to validate if two answers are semantically equivalent.

    Returns:
        dict with 'is_valid' (bool) and 'explanation' (str)
    """
    prompt = f"""You are a strict answer validator. Given a question and two answers, determine if they are semantically equivalent (i.e., they convey the same information/meaning).

Question: {question}

Answer A (Model's answer): {model_answer}

Answer B (Ground truth): {ground_truth}

Are these two answers semantically equivalent? Consider:
- Numbers should match exactly
- Names should match exactly
- The core meaning should be the same (minor phrasing differences are OK)

Respond with ONLY valid JSON:
{{"is_same": true/false, "explanation": "brief reason"}}

JSON:"""

    messages = [
        {"role": "user", "content": prompt}
    ]

    try:
        inputs = tokenizer.apply_chat_template(
            messages,
            add_generation_prompt=True,
            tokenize=True,
            return_tensors="pt",
            return_dict=True,
            truncation=True,
            max_length=2048,
        ).to(model.device)

        input_len = inputs["input_ids"].shape[-1]

        with torch.no_grad():
            outputs = model.generate(
                **inputs,
                max_new_tokens=max_new_tokens,
                do_sample=False,
            )

        new_tokens = outputs[0, input_len:]
        raw = tokenizer.decode(new_tokens, skip_special_tokens=True).strip()

        # Parse JSON
        start = raw.find("{")
        end = raw.rfind("}") + 1
        if start != -1 and end > start:
            parsed = json.loads(raw[start:end])
            return {
                "is_valid": parsed.get("is_same", False),
                "explanation": parsed.get("explanation", ""),
                "raw": raw
            }
        else:
            return {"is_valid": False, "explanation": "Failed to parse validation response", "raw": raw}

    except Exception as e:
        return {"is_valid": False, "explanation": f"Validation error: {str(e)}", "raw": ""}


def validate_answer_groq(model_answer, ground_truth, question, max_retries=2):
    """
    Use Groq API to validate if two answers are semantically equivalent.

    Returns:
        dict with 'is_valid' (bool) and 'explanation' (str)
    """
    prompt = f"""You are a strict answer validator. Given a question and two answers, determine if they are semantically equivalent (i.e., they convey the same information/meaning).

Question: {question}

Answer A (Model's answer): {model_answer}

Answer B (Ground truth): {ground_truth}

Are these two answers semantically equivalent? Consider:
- Numbers should match exactly
- Names should match exactly
- The core meaning should be the same (minor phrasing differences are OK)

Respond with ONLY valid JSON:
{{"is_same": true, "explanation": "brief reason"}} or {{"is_same": false, "explanation": "brief reason"}}

JSON:"""

    for attempt in range(max_retries):
        try:
            response = groq_client.chat.completions.create(
                model="llama-3.3-70b-versatile",
                messages=[{"role": "user", "content": prompt}],
                temperature=0.0,
                max_tokens=128,
            )

            raw = response.choices[0].message.content.strip()

            # Parse JSON
            start = raw.find("{")
            end = raw.rfind("}") + 1
            if start != -1 and end > start:
                parsed = json.loads(raw[start:end])
                return {
                    "is_valid": parsed.get("is_same", False),
                    "explanation": parsed.get("explanation", ""),
                    "raw": raw
                }
            else:
                return {"is_valid": False, "explanation": "Failed to parse validation response", "raw": raw}

        except Exception as e:
            error_str = str(e)
            print(f"Validation attempt {attempt + 1} failed: {error_str}")
            if attempt == max_retries - 1:
                return {"is_valid": False, "explanation": f"Validation error: {error_str}", "raw": ""}
            time.sleep(1)

    return {"is_valid": False, "explanation": "Max retries exceeded", "raw": ""}


def validate_answer(model_answer, ground_truth, question):
    """
    Main validation function - routes to local or Groq based on use_groq flag.

    Args:
        model_answer: The answer generated by the model
        ground_truth: The expected correct answer
        question: The original question (for context)

    Returns:
        dict with 'is_valid' (bool), 'explanation' (str), and 'raw' (str)
    """
    # Quick exact match check first (case-insensitive, stripped)
    if model_answer.strip().lower() == ground_truth.strip().lower():
        return {"is_valid": True, "explanation": "Exact match", "raw": ""}

    # If not exact match, use model to check semantic equivalence
    if use_groq == 1:
        return validate_answer_groq(model_answer, ground_truth, question)
    else:
        return validate_answer_local(model_answer, ground_truth, question)


def make_model_input(example):
    return {
        "question": example["question"],
        "question_date": example["question_date"],
        "haystack_dates": example["haystack_dates"],
        "haystack_session_ids": example["haystack_session_ids"],
        "answer_session_ids": example["answer_session_ids"],
        "haystack_session_ids": example["haystack_session_ids"],
        "question_type": example["question_type"],
        "haystack_sessions": [
            [
                {
                    "role": turn["role"],
                    "content": turn["content"],
                    # Edited 1/15/2026
                    "has_answer": turn["has_answer"]
                }
                for turn in session
            ]
            for session in example["haystack_sessions"]
        ],
    }


def get_label(example):
    return {
        "id": example["question_id"],
        "answer": example["answer"],
    }

def save_example(example, out_dir="."):
    # Number of sessions
    num_sessions = len(example["haystack_sessions"])

    # Get question_id and make sure it's filename-safe
    qid = example["question_id"]

    # Build filename like "3_gpt4_2655b836.json"
    filename = f"{num_sessions}_{qid}.json"
    path = os.path.join(out_dir, filename)

    # Save to disk
    with open(path, "w", encoding="utf-8") as f:
        json.dump(example, f, ensure_ascii=False, indent=2)

    return path


# Default Approach

In [9]:
from transformers import pipeline, BitsAndBytesConfig, set_seed
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch
from google.colab import userdata
import time

# =============================================================================
# MODEL SELECTION FLAG
# =============================================================================
# use_groq = 0  -> Use local Llama 8B model (default)
# use_groq = 1  -> Use Groq API with Llama 3.3 70B
# =============================================================================
use_groq = 0

# Setup based on flag
if use_groq == 0:
    # --- LOCAL MODEL SETUP ---
    os.environ['HF_CACHE'] = '/content/drive/My Drive/transformers_cache'
    hf_token = userdata.get('HF_TOKEN')
    os.environ['HF_TOKEN'] = hf_token

    set_seed(1234)

    local_model_flag = 0
    if local_model_flag == 0:
        model_name = "nvidia/Llama-3.1-Nemotron-Nano-8B-v1"
    elif local_model_flag == 1:
        model_name = "google/gemma-2-9b-it"

    bnb_cfg = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_compute_dtype=torch.bfloat16,
        bnb_4bit_use_double_quant=True,
        bnb_4bit_quant_type="nf4",
    )

    tokenizer = AutoTokenizer.from_pretrained(model_name)

    model = AutoModelForCausalLM.from_pretrained(
        model_name,
        quantization_config=bnb_cfg,
        device_map="auto",
    )
    model.eval()

    print(f"Loaded local model: {model_name}")
    print(f"Device: {model.device}, Dtype: {next(model.parameters()).dtype}")

    groq_client = None  # Not used

else:
    # --- GROQ API SETUP ---
    from groq import Groq

    groq_key = userdata.get('groq_key')
    groq_client = Groq(api_key=groq_key)
    model_name = "llama-3.3-70b-versatile"

    # Set placeholders for local model vars (not used)
    model = None
    tokenizer = None

    print(f"Using Groq API with model: {model_name}")


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Loaded local model: nvidia/Llama-3.1-Nemotron-Nano-8B-v1
Device: cuda:0, Dtype: torch.float16


In [12]:
import os
import json
import torch

out_dir = "lme_jsons"
reset = False

# =============================================================================
# CONFIGURATION FLAGS
# =============================================================================
validate_responses = True   # Set to False to skip validation and save all responses
save_failed_to_file = True  # Save failed IDs to a file for persistence across sessions

# =============================================================================
# TRACKING SETS
# =============================================================================
# 1) Build a set of already-processed question_ids from existing files
processed_ids = set()

# 2) Runtime set of failed question_ids (answers didn't match ground truth)
failed_ids = set()

# 3) Load previously failed IDs from file (if exists) to avoid retrying
failed_ids_file = os.path.join(out_dir, "_failed_ids.json")

if os.path.isdir(out_dir):
    if reset:
        for filename in os.listdir(out_dir):
            file_path = os.path.join(out_dir, filename)
            if os.path.isfile(file_path):
                os.remove(file_path)
                print(f'{filename} removed')
        failed_ids = set()  # Clear failed IDs on reset
    else:
        # Load processed IDs from saved JSON files
        for fname in os.listdir(out_dir):
            if not fname.endswith(".json"):
                continue
            if fname.startswith("_"):  # Skip meta files like _failed_ids.json
                continue
            base = os.path.splitext(fname)[0]
            parts = base.split("_", 1)
            if len(parts) != 2:
                continue
            _, qid = parts
            processed_ids.add(qid)

        # Load previously failed IDs
        if os.path.exists(failed_ids_file):
            with open(failed_ids_file, "r") as f:
                failed_ids = set(json.load(f))
            print(f"Loaded {len(failed_ids)} previously failed IDs from file")
else:
    os.makedirs(out_dir, exist_ok=True)

print(f"Found {len(processed_ids)} existing successful test files")
print(f"Found {len(failed_ids)} previously failed test IDs")

# =============================================================================
# HELPER FUNCTION TO SAVE FAILED IDS
# =============================================================================
def save_failed_ids():
    """Persist failed IDs to file for next session."""
    if save_failed_to_file:
        with open(failed_ids_file, "w") as f:
            json.dump(list(failed_ids), f, indent=2)
        print(f"Saved {len(failed_ids)} failed IDs to {failed_ids_file}")

# =============================================================================
# MAIN PROCESSING LOOP
# =============================================================================
# Statistics tracking
stats = {
    "processed": 0,
    "skipped_already_done": 0,
    "skipped_previously_failed": 0,
    "skipped_too_many_sessions": 0,
    "validation_passed": 0,
    "validation_failed": 0,
    "errors": 0,
}

try:
    for i, test in enumerate(LME):
        qid = test["question_id"]

        # Skip if already successfully processed
        if qid in processed_ids:
            stats["skipped_already_done"] += 1
            continue

        # Skip if previously failed validation (don't retry known failures)
        if qid in failed_ids:
            print(f"[SKIP-FAILED] Question ID {qid} previously failed validation, skipping.")
            stats["skipped_previously_failed"] += 1
            continue

        # Skip if too many sessions
        if len(test['haystack_dates']) > 4:
            stats["skipped_too_many_sessions"] += 1
            continue

        trimmed_example = make_model_input(test)
        print(f"\n{'='*60}")
        print(f"Question ID {qid} has {len(test['haystack_dates'])} session haystacks")
        print(f"Question: {test['question']}")
        print(f"Ground Truth: {test['answer']}")

        # Generate annotation
        annot = cot_annotate(trimmed_example)
        print(f"Model Output: {json.dumps(annot, indent=2)}")

        stats["processed"] += 1

        # Check for errors or parsing failures
        if "error" in annot:
            print(f"[ERROR] {annot['error']}")
            stats["errors"] += 1
            failed_ids.add(qid)
            continue

        if "raw" in annot:
            print(f"[ERROR] Non-JSON response")
            stats["errors"] += 1
            failed_ids.add(qid)
            continue

        # Get model's answer
        model_answer = annot.get("answer", "")
        ground_truth = test["answer"]

        # =================================================================
        # VALIDATION STEP
        # =================================================================
        if validate_responses:
            print(f"\n[VALIDATING] Model answer vs Ground truth...")
            validation_result = validate_answer(model_answer, ground_truth, test["question"])
            print(f"Validation: is_valid={validation_result['is_valid']}, explanation={validation_result['explanation']}")

            if not validation_result["is_valid"]:
                print(f"[VALIDATION FAILED] Discarding response for {qid}")
                stats["validation_failed"] += 1
                failed_ids.add(qid)
                continue
            else:
                print(f"[VALIDATION PASSED] Saving response for {qid}")
                stats["validation_passed"] += 1

        # =================================================================
        # SAVE SUCCESSFUL RESPONSE
        # =================================================================
        if "model_annotations" not in test:
            test["model_annotations"] = {}

        test["model_annotations"][model_name] = {
            "status": "ok",
            "reasoning": annot.get("reasoning"),
            "answer": annot.get("answer"),
        }

        save_example(test, out_dir=out_dir)
        processed_ids.add(qid)  # Add to processed set
        print(f"[SAVED] {qid}")

        # Periodic cleanup
        if stats["processed"] % 20 == 0:
            torch.cuda.empty_cache()
            save_failed_ids()  # Periodic save of failed IDs

        # Optional: break after N examples for testing
        if stats["processed"] >= 50:
            print("\n[STOPPING] Reached 50 processed examples")
            break

except KeyboardInterrupt:
    print("\n[INTERRUPTED] Saving failed IDs before exit...")

finally:
    # Always save failed IDs at the end
    save_failed_ids()

    # Print final statistics
    print("\n" + "="*60)
    print("FINAL STATISTICS")
    print("="*60)
    for key, value in stats.items():
        print(f"  {key}: {value}")
    print(f"  total_failed_ids: {len(failed_ids)}")
    print(f"  total_processed_ids: {len(processed_ids)}")


The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


Loaded 0 previously failed IDs from file
Found 0 existing successful test files
Found 0 previously failed test IDs

Question ID gpt4_2655b836 has 3 session haystacks
Question: What was the first issue I had with my new car after its first service?
Ground Truth: GPS system not functioning correctly
[FILTER] kept 3 / 3 sessions (0 removed).
Text length 762
temporal-reasoning


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


Model Output: {
  "reasoning": "The first issue with the new car after its first service (March 15th) was reported on March 22nd, which is after the service date.",
  "answer": "the GPS system issue"
}

[VALIDATING] Model answer vs Ground truth...


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

Model Output: {
  "reasoning": "The user mentioned attending a cultural festival 'yesterday' and started Spanish classes 'three months ago'. Since 'yesterday' is a time closer to the present than 'three months ago', the cultural festival happened later than the start of Spanish classes.",
  "answer": "the start of my Spanish classes"
}

[VALIDATING] Model answer vs Ground truth...


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


Validation: is_valid=True, explanation=Both answers refer to the same event, just phrased differently.
[VALIDATION PASSED] Saving response for gpt4_5438fa52
[SAVED] gpt4_5438fa52

Question ID gpt4_c27434e8 has 2 session haystacks
Question: Which project did I start first, the Ferrari model or the Japanese Zero fighter plane model?
Ground Truth: Japanese Zero fighter plane model
[FILTER] kept 2 / 2 sessions (0 removed).
Text length 652
temporal-reasoning


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


Model Output: {
  "reasoning": "The user mentioned starting the Ferrari 288 GTO model about three weeks ago and the Japanese Zero fighter plane model about a month ago. Since a month ago is earlier than three weeks ago, the Japanese Zero fighter plane model was started first.",
  "answer": "the Japanese Zero fighter plane model"
}

[VALIDATING] Model answer vs Ground truth...
Validation: is_valid=True, explanation=Both answers refer to the same project, the Japanese Zero fighter plane model.
[VALIDATION PASSED] Saving response for gpt4_c27434e8
[SAVED] gpt4_c27434e8

[STOPPING] Reached 50 processed examples
Saved 24 failed IDs to lme_jsons/_failed_ids.json

FINAL STATISTICS
  processed: 50
  skipped_already_done: 0
  skipped_previously_failed: 0
  skipped_too_many_sessions: 2
  validation_passed: 26
  validation_failed: 24
  errors: 0
  total_failed_ids: 24
  total_processed_ids: 26


Current issue is that despite having the model prompting to get the user preferences, the model is not sophisticated enough to pull actual preferences... while a similar prompt for something like GPT 5 would give you something closer to the answer label

In [13]:
%%capture
!zip -r lme_jsons.zip lme_jsons

# Distillation with Groq

In [ ]:
import os
from groq import Groq
import google.generativeai as genai
from google.colab import userdata

groq_key = userdata.get('groq_key')
groq_client = Groq(api_key = groq_key)

In [ ]:
def generate_rationale_groq(history_text, question, ground_truth_answer, max_retries=3):
    """Generate reasoning trace using Llama 3.3 70B via Groq (free)."""

    prompt = f"""You are helping build a training dataset for a reasoning model.

Given a conversation history and a question, generate a detailed step-by-step reasoning trace
that shows HOW to find the answer. The reasoning should:
1. Identify what information is needed to answer the question
2. Locate the specific session(s) and turn(s) containing relevant information
3. Extract and synthesize the key facts
4. Arrive at the final answer

CONVERSATION HISTORY:
{history_text}

QUESTION: {question}

GROUND TRUTH ANSWER: {ground_truth_answer}

Generate a reasoning trace that would lead to this answer. Be specific about which
parts of the conversation contain the relevant information.

Respond in this exact JSON format:
{{
    "reasoning": "Step 1: [identify what we need to find]\\nStep 2: [locate relevant information in Session X, Turn Y]\\nStep 3: [extract key facts]\\nStep 4: [synthesize to get answer]",
    "answer": "[final answer matching ground truth]"
}}

JSON:"""

    for attempt in range(max_retries):
        try:
            response = groq_client.chat.completions.create(
                model="llama-3.3-70b-versatile",  # Free, very capable
                messages=[{"role": "user", "content": prompt}],
                temperature=0.1,
                max_tokens=1024,
            )

            raw = response.choices[0].message.content.strip()

            # Parse JSON
            start = raw.find("{")
            end = raw.rfind("}") + 1
            if start != -1 and end > start:
                parsed = json.loads(raw[start:end])
                return {"status": "success", **parsed}
            else:
                return {"status": "parse_error", "raw": raw}

        except Exception as e:
            if attempt == max_retries - 1:
                return {"status": "error", "error": str(e)}
            time.sleep(2 ** attempt)  # Exponential backoff

    return {"status": "max_retries_exceeded"}


def generate_rationale_gemini(history_text, question, ground_truth_answer):
    """Fallback/alternative using Gemini 1.5 Flash (free)."""

    prompt = f"""You are helping build a training dataset. Given conversation history and a question,
generate a step-by-step reasoning trace showing how to find the answer.

CONVERSATION HISTORY:
{history_text}

QUESTION: {question}
GROUND TRUTH ANSWER: {ground_truth_answer}

Generate detailed reasoning that identifies which session/turn contains the answer.

Respond as JSON: {{"reasoning": "...", "answer": "..."}}"""

    try:
        response = gemini_model.generate_content(prompt)
        raw = response.text.strip()

        start = raw.find("{")
        end = raw.rfind("}") + 1
        if start != -1 and end > start:
            parsed = json.loads(raw[start:end])
            return {"status": "success", **parsed}
        return {"status": "parse_error", "raw": raw}

    except Exception as e:
        return {"status": "error", "error": str(e)}


In [ ]:
import json
import time
from tqdm import tqdm

def build_reasoning_dataset(lme_examples, output_dir="reasoning_dataset", use_groq=True):
    """
    Build dataset where each example has:
    - input (conversation + question)
    - reasoning trace (from teacher model)
    - answer
    """

    os.makedirs(output_dir, exist_ok=True)

    results = []

    for i, example in enumerate(tqdm(lme_examples)):
        qid = example["question_id"]
        question = example["question"]
        ground_truth = example["answer"]
        question_type = example["question_type"]

        # Build history text (using your existing function)
        history_text = build_history_text_answer_sessions(example, max_chars=30000)

        # Generate rationale from teacher model
        if use_groq:
            teacher_output = generate_rationale_groq(
                history_text, question, ground_truth
            )
        else:
            teacher_output = generate_rationale_gemini(
                history_text, question, ground_truth
            )

        # Build the dataset entry
        entry = {
            "question_id": qid,
            "question_type": question_type,
            "question": question,
            "ground_truth_answer": ground_truth,
            "conversation_history": history_text,
            "teacher_model": "llama-3.3-70b" if use_groq else "gemini-1.5-flash",
            "teacher_output": teacher_output,
        }

        # If successful, also create the "ideal" training format
        if teacher_output.get("status") == "success":
            entry["training_input"] = (
                f"Conversation history:\n{history_text}\n\n"
                f"Question: {question}\n\n"
                f"Think step by step, then provide your answer as JSON with "
                f"'reasoning' and 'answer' keys."
            )
            entry["training_output"] = json.dumps({
                "reasoning": teacher_output["reasoning"],
                "answer": teacher_output["answer"]
            }, indent=2)

        results.append(entry)

        # Save incrementally
        output_path = os.path.join(output_dir, f"{qid}.json")
        with open(output_path, "w") as f:
            json.dump(entry, f, indent=2)

        # Rate limiting for free tiers
        time.sleep(0.5)  # Groq is fast, but be respectful

        # Progress update
        if (i + 1) % 10 == 0:
            success_count = sum(1 for r in results if r["teacher_output"].get("status") == "success")
            print(f"Processed {i+1}, Success rate: {success_count}/{len(results)}")

    # Save full dataset
    with open(os.path.join(output_dir, "full_dataset.json"), "w") as f:
        json.dump(results, f, indent=2)

    return results


In [ ]:
examples_to_process = [ex for ex in LME if len(ex['haystack_dates']) <= 4]

# Playground
examples_to_process[0:5]

print(f"Processing {len(examples_to_process)} examples...")
dataset = build_reasoning_dataset(examples_to_process[0:5], use_groq=True)

Processing 486 examples...


  0%|          | 0/5 [00:00<?, ?it/s]

[FILTER] kept 3 / 3 sessions (0 removed).
Text length 42301
[HIT TXT TRUNCATION at 30000]


 20%|██        | 1/5 [00:03<00:14,  3.71s/it]

[FILTER] kept 2 / 2 sessions (0 removed).
Text length 34426
[HIT TXT TRUNCATION at 30000]


...

 60%|██████    | 3/5 [00:11<00:07,  3.66s/it]

[FILTER] kept 2 / 2 sessions (0 removed).
Text length 26439


 80%|████████  | 4/5 [00:14<00:03,  3.66s/it]

[FILTER] kept 2 / 2 sessions (0 removed).
Text length 35679
[HIT TXT TRUNCATION at 30000]


100%|██████████| 5/5 [00:18<00:00,  3.66s/it]


In [ ]:
dataset

[{'question_id': 'gpt4_2655b836',
  'question_type': 'temporal-reasoning',
  'question': 'What was the first issue I had with my new car after its first service?',
  'ground_truth_answer': 'GPS system not functioning correctly',
  'conversation_history': 'tailer has liability insurance to protect your vehicle in case of damage or accidents.\n8. **Check their experience with your vehicle type**: If you have a specialty or high-performance vehicle, ensure the detailer has experience working with similar vehicles.\n9. **Check their turnaround time**: Find out how long the detailing process will take and whether they offer express or priority services if you\'re short on time.\n10. **Trust your instincts**: If something feels off or you don\'t click with the detailer, trust your instincts and look for someone else. You want to feel confident that your vehicle is in good hands.\n\nAdditionally, here are some red flags to watch out for:\n\n* Unrealistically low prices\n* Lack of transparency